# Optimization Problem Time Series

This notebook optimizes an electrci mix based on : 
- an electricity demand time serie
- a PV production time serie
- a wind production time serie

In [6]:
import numpy as np
import pandas as pd
from scipy.optimize import minimize
from pulp import *
import sys
from utilities import import_excel
import plotly.graph_objects as go
import plotly.express as px
import pickle

In [7]:
# import gurobipy as gp

# options = {
#     "WLSACCESSID":"1b1f64ca-fe52-4c0c-bf3f-74d35bd43d51",
#     "WLSSECRET":"431b8c8e-287c-476c-849c-b206b4e81924",
#     "LICENSEID":2503220,
# }

Enter country name for file naming: 

In [51]:
country_name = 'California'
year = 2021

### Load Time Series

First we load the time series that will be used in the problem. We use the  ```import_excel``` function used in the wavelet decomposition.

In [52]:
# Demand time serie

dpd = 24 # data per day in the time serie
dpy = 365 # data per year :  cut the leap years to 365 years


ndpd = 24 # new data per day for hourly data (for the interpolation)
signal_length = ndpd * dpy

# Directory path
path_input_data = '../input_time_series/'

# !!! CHANGE FILENAME HERE !!!
# file_name = 'Spain/Espagne_load_entsoe_2021.xlsx'
file_name = 'California/California_2021_hourly_demand_MWh.xlsx'
# file_name = 'Japan/Japan_demand_Plexos_2015.xlsx'
# file_name = '/France/FR_demand_artificial_2021-2022.xlsx'
Load_ts = import_excel(path_input_data,file_name, 
                                    dpd ,ndpd, dpy, 
                                    interp=True, norm = 'max') # interpolate data from dpd to ndpd numper of points per day

mean_load = pd.read_excel(path_input_data+file_name).mean().iloc[0]

In [53]:
mean_load

25020.717979452056

In [54]:
# Wind time serie 

dpd = 4 # data per day
dpy = 365 # data per year :  cut the leap years to 365 years

# We interpolate so that we have hourly data
ndpd = 24 # new data per day for hourly data (for the interpolation)
signal_length = ndpd * dpy

# Directory path
path_input_data = '../input_time_series/'

# !!! CHANGE FILENAME HERE !!!
# file_name = 'Spain/Wind_generation_ES_2021_intermittent.xlsx'
file_name = 'California/Wind_onshore_energy_California_2021_intermittent.xlsx'
# file_name = 'Japan/Wind_energy_generation_2022_Japan_intermittent.xlsx'
# file_name = 'France/Wind_onshore_energy_France_2021_intermittent.xlsx'
Wind_ts = import_excel(path_input_data,file_name, 
                                    dpd ,ndpd, dpy, 
                                    interp=True, norm = 'max') # interpolate data from dpd to ndpd numper of points per day
mean_wind = pd.read_excel(path_input_data+file_name).mean().iloc[0]

In [55]:
Wind_ts.mean()

0.41622370499966915

In [56]:
# PV time serie

dpd = 24 # data per day
dpy = 365 # data per year :  cut the leap years to 365 years


# We interpolate so that we have hourly data
ndpd = 24 # new data per day (for the interpolation)
signal_length = ndpd * dpy

#
# Directory path
path_input_data = '../input_time_series/'

# !!! CHANGE FILENAME HERE !!!
# file_name='Spain/ren_ninja_pv_ES_2019.xlsx'
# file_name = 'Spain/Solar_generation_ES_2021_intermittent.xlsx'
file_name='California/California_2021_hourly_solar_MWh.xlsx'
# file_name = 'Japan/Solar_energy_generation_2022_Japan_intermittent.xlsx'
# file_name = 'France/Solar_energy_France_2021_intermittent.xlsx'
PV_ts = import_excel(path_input_data,file_name, 
                                    dpd ,ndpd, dpy, 
                                    interp=True, norm = 'max') # interpolate data from dpd to ndpd numper of points per day
mean_pv =  pd.read_excel(path_input_data+file_name).mean().iloc[0]

In [57]:
# Create a Plotly figure
fig = go.Figure()

fig.add_trace(go.Scatter(y=PV_ts, mode='lines', name='PV'))
fig.add_trace(go.Scatter(y=Load_ts, mode='lines', name='Demand'))
fig.add_trace(go.Scatter(y=Wind_ts, mode='lines', name='Wind'))
fig.update_layout(title=f'{country_name} 2021', xaxis_title='Day', yaxis_title='Energy normalized')

# Show the plot
fig.show()

### Description of the problem

#### Equations:

- **Objective function** : 
  - Minimize dispatchable energy: $ \min(\sum{P_{dispatchable}(t)*dt}) $


- **Node Law** : 
  - $(P_{pv}(t) + P_{wind}(t) + P_{dispatchable}(t) - P_{in\_stock}(t) + P_{out\_stock}(t) = P_{demand}(t) + P_{curt}(t))$


- **State of charge**
  - $SOC(t+1)=SOC(t)+P_{in\_stock}(t) - P_{out\_stock}(t)$

#### Contraintes :
- $E_{wind} + E_{pv} \leq E_{demand}$
- We want a maximum storage size of 10 hours:  $E_{stock} \leq 10$
- Charging and discharging at the same time is not possible. 


### Implementation
#### Decision Variables:
- `x_pv`: Installed capacity for photovoltaic production.
- `x_wind`: Installed capacity for wind production.
- `ts_dispatchable`: Dispatchable production (can be controlled), time serie.
- `p_ch`: Battery charging power, time serie.
- `p_dech`: Battery discharging power, time serie.
- `SOC_ts`: State of charge of the battery, time serie.
- `p_curt`: Curtailment power (lost energy), time serie.
- `dech_active`: Binary variable indicating if the battery is charging or discharging.

### Run the optimization with GUROBI

**If the optimization has already been run, go to the next part where results can be loaded and analysed in plots.**

In [58]:
prob = LpProblem(f"myProblem_{country_name}", LpMinimize)
signal_length = len(Load_ts)

dt = 1 # hour
e_factor = 10 # max hours of consumption to be stored
E_max = e_factor*Load_ts.mean()# max capacity of storage (MW)
stock_efficiency = 0.8 # %
P_max = 100000 # MW used for the binary variable, voluntraily very high

# Decision Variables
x_pv = LpVariable("PV_coefficient", lowBound=0)
x_wind = LpVariable("Wind_coefficient", lowBound=0)
ts_dispatchable = LpVariable.dicts('Dispatchable_production', range(signal_length), lowBound=0 )
p_ch = LpVariable.dicts('Pch', range(signal_length), lowBound=0, upBound = P_max)
p_dech = LpVariable.dicts('Pdech', range(signal_length), lowBound=0, upBound = P_max)
SOC_ts = LpVariable.dicts('Stock',range(signal_length), lowBound=0, upBound=E_max )
#TODO : changer upBound curtailment
p_curt = LpVariable.dicts('Curtailment',range(signal_length), lowBound=0, upBound=0.01)
dech_active = LpVariable.dicts('Dech_active', range(signal_length), cat='Binary')


# Constraint 1: nodal law
for t in range(len(Load_ts)):
    prob += x_pv * PV_ts[t] + ts_dispatchable[t] + x_wind * Wind_ts[t]+p_dech[t] == Load_ts[t]  +p_ch[t]+p_curt[t]

# Constraint 2: storage
for t in range(1, signal_length):
    prob += SOC_ts[t] == SOC_ts[t-1] + (stock_efficiency*p_ch[t]-p_dech[t])*dt
 
    # Binary variable: can't charge and discharge at the same time
    prob += p_ch[t] <= (1-dech_active[t])*P_max 
    prob += p_dech[t] <= (dech_active[t])*P_max

#TODO : trouver une mailleure contrainte pour p_stock
prob+= p_ch[0]==0
prob+=p_dech[0]==0
prob += SOC_ts[0] == SOC_ts[signal_length-1] #same state of charge at the start and end


prob += x_pv*PV_ts.sum()+x_wind*Wind_ts.sum() <= Load_ts.sum()

# Fonction objectif
prob += lpSum(ts_dispatchable.values())*dt

# Write problem in file 
prob.writeLP(f"myProblem_{country_name}.lp")


prob.solve(GUROBI(0.01))

# Afficher les résultats
print("Status:", LpStatus[prob.status])
print("Coefficient optimal pour PV:", x_pv.varValue)
print("Coefficient optimal pour Wind:", x_wind.varValue)


Gurobi Optimizer version 11.0.1 build v11.0.1rc0 (win64 - Windows 10.0 (19045.2))

CPU model: 11th Gen Intel(R) Core(TM) i5-1145G7 @ 2.60GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Academic license 2503220 - for non-commercial use only - registered to du___@ethz.ch
Optimize a model with 35041 rows, 52561 columns and 122623 nonzeros
Model fingerprint: 0x9deaa9c0
Variable types: 43802 continuous, 8759 integer (0 binary)
Coefficient statistics:
  Matrix range     [8e-05, 1e+05]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e-02, 1e+05]
  RHS range        [4e-01, 1e+05]
Found heuristic solution: objective 5025.3694715
Presolve removed 4 rows and 8764 columns
Presolve time: 4.21s
Presolved: 35037 rows, 43797 columns, 115002 nonzeros
Variable types: 35038 continuous, 8759 integer (8759 binary)
Deterministic concurrent LP optimizer: primal and dual simplex
Showing primal log only...


Root simplex log...

It

: 

: 

### Save the results

In [20]:
folder_path = f'results/{country_name}'
import os
if not os.path.exists(folder_path):
    os.makedirs(folder_path)

In [21]:
# Get results of optimization 
optimized_pv = [x_pv.varValue * PV_ts[t] for t in range(signal_length)]
optimized_wind = [x_wind.varValue * Wind_ts[t] for t in range(signal_length)]
optimized_dispatchable = [ts_dispatchable[t].varValue for t in range(signal_length)]
optimized_stock = [SOC_ts[t].varValue for t in range(signal_length)]
optimized_p_curt = [p_curt[t].varValue for t in range(signal_length)]
optimized_charge = [p_ch[t].varValue for t in range(signal_length)]
optimized_discharge = [p_dech[t].varValue for t in range(signal_length)]

In [41]:
# Bar chart
E_wind = np.sum(optimized_wind)*mean_load
E_pv = np.sum(optimized_pv)*mean_load
E_dispatch = np.sum(optimized_dispatchable)*mean_load
E_curt = np.sum(optimized_p_curt)*mean_load
E_loss  = (np.sum(optimized_charge)-np.sum(optimized_discharge))*mean_load
E_stock = np.sum(optimized_charge)*mean_load
E_destock = np.sum(optimized_discharge)*mean_load

In [42]:
results = {
    'optimized_pv': optimized_pv,
    'optimized_wind': optimized_wind,
    'optimized_dispatchable': optimized_dispatchable,
    'optimized_stock':optimized_stock, 
    'optimized_charge': optimized_charge, 
    'optimized_discharge':optimized_discharge, 
    'optimized_p_curt' : optimized_p_curt,
    'consumption':np.array(Load_ts), 
    'pv_capacity': x_pv.varValue, 
    'wind_capacity': x_wind.varValue,
    'E_wind' : E_wind, 
    'E_pv':E_pv, 
    'E_dispatch':E_dispatch, 
    'E_curt':E_curt, 
    'E_loss':E_loss, 
    'E_stock':E_stock,
    'E_destock':E_destock
}

filename = f'results/{country_name}/optimization_results_curtail_0.01_mean_load.pickle'

with open(filename, 'wb') as pickle_file:
    pickle.dump(results, pickle_file)

print(f"Optimization results saved to "+filename)

Optimization results saved to results/France/optimization_results_curtail_0.01_mean_load.pickle


### Read results stored in pickle file

In [34]:
country_name = 'France'

In [35]:
data = pd.read_pickle(f"results/{country_name}/optimization_results_curtail_0.01_mean_load.pickle")

In [36]:
optimized_pv = data['optimized_pv']
optimized_wind = data['optimized_wind']
optimized_charge = data['optimized_charge']
optimized_discharge = data['optimized_discharge']
optimized_p_curt = data['optimized_p_curt']
optimized_stock = data['optimized_stock']
optimized_dispatchable = data['optimized_dispatchable']
Load_ts = data['consumption']

### Plots

In [26]:
from plots import plot_ts_optim, plot_pie_energy, plot_storage, plot_stack_production
colors_dict = {
    'Wind': 'rgb(255, 128, 128)',        
    'PV': 'rgb(128, 255, 128)',
    'Discharge': '#ff7f0e',    
    'SOC': '#2ca02c',           
    'Charge': '#9467bd',
    'Consumption': '#e377c2',          
    'Dispatchable': 'rgb(128, 128, 255)',       
    'Curtailment': '#17becf'    
}

In [27]:
plot_ts_optim([optimized_pv, optimized_wind, optimized_dispatchable, optimized_p_curt,np.array(Load_ts) ], ['PV', 'Wind', 'Dispatchable', 'Curtailment', 'Consumption'], country_name, savefig=False)

In [28]:
plot_storage(optimized_charge, optimized_discharge, optimized_stock, country_name, savefig=False)

In [29]:
plot_stack_production(optimized_pv, optimized_wind, optimized_dispatchable, country_name)

## Diagrammes et graphes

In [37]:
mean_load

52347.48875570776

In [38]:
# Bar chart
E_wind = np.sum(optimized_wind)*mean_load
E_pv = np.sum(optimized_pv)*mean_load
E_dispatch = np.sum(optimized_dispatchable)*mean_load
E_curt = -np.sum(optimized_p_curt)*mean_load
E_loss  = -(np.sum(optimized_charge)-np.sum(optimized_discharge))*mean_load
E_stock = np.sum(optimized_charge)*mean_load
E_destock = np.sum(optimized_discharge)*mean_load

In [31]:

# fig = go.Figure(data=[
#     go.Bar(name='Wind', x=[country_name], y=[E_wind]),
#     go.Bar(name='PV', x=[country_name], y=[E_pv]),
#     go.Bar(name='Dispatchable', x=[country_name], y=[E_dispatch]),
#     go.Bar(name='Curtailment', x=[country_name], y=[E_curt]),
#     go.Bar(name='Loss', x=[country_name], y=[E_loss])
# ])

# fig.update_layout(
#     title='Energy production',
#     barmode='relative',
#     yaxis_title = 'MWh'
# )

# fig.show()

In [32]:
def plot_pie_energy(list_energy, country_name, names = ['Wind', 'PV', 'Dispatchable'], colors_dict = colors_dict, savefig=False):
    fig = px.pie(names=names,
                values=list_energy,
                color_discrete_sequence= [colors_dict['Wind'], colors_dict['PV'], colors_dict['Dispatchable']],  # Utiliser color_discrete_sequence pour définir les couleurs
                title='Energy Production')
    fig = go.Figure(data=[go.Pie(labels=['Wind', 'PV', 'Dispatchable'], values=[E_wind, E_pv, E_dispatch], marker=dict(colors=[colors_dict['Wind'], colors_dict['PV'], colors_dict['Dispatchable']]))])

    fig.update_traces(textposition='inside', textinfo='percent+label')
    # Write HTML file
    if savefig:
        fig.write_html(f"figures/{country_name}_optim_pie_chart.html")

    # Show the plot
    fig.show()
    return

In [33]:
plot_pie_energy([E_wind, E_pv, E_dispatch], country_name)

In [66]:
# Bar chart

E_wind = np.sum(optimized_wind)*mean_load
E_pv = np.sum(optimized_pv)*mean_load
E_dispatch = np.sum(optimized_dispatchable)*mean_load
E_curt = np.sum(optimized_p_curt)*mean_load
E_loss  =(np.sum(optimized_charge)-np.sum(optimized_discharge))*mean_load
E_stock = np.sum(optimized_charge)*mean_load
E_destock = np.sum(optimized_discharge)*mean_load

In [67]:
# Sankey

sources = ['Wind', 'PV', 'Dispatchable','Production', 'Consumption', 'Loss', 'Curtailment']
E_production = E_wind + E_pv + E_dispatch
E_consumption = Load_ts.mean()

# Définition des valeurs d'énergie pour chaque source
values = [E_wind, E_pv, E_dispatch, E_production, E_consumption, E_loss, E_curt]  # Assurez-vous que la somme est égale à 100 ou à la valeur totale d'énergie

# Création des liens entre les sources
link_source = [0, 1, 2, 3, 3,  3]  # Les index 0, 1 et 2 représentent les sources Wind, PV et Dispatchable, respectivement.
link_target = [3, 3, 3, 4, 5, 6, 7 ]  # L'index 3 représente la source "Output"
link_value = values  # Les valeurs sont celles des énergies calculées
colors = ['rgba(31, 119, 180, 0.8)', 'rgba(255, 127, 14, 0.8)', 'rgba(44, 160, 44, 0.8)', 'rgba(214, 39, 40, 0.8)', 
          'rgba(148, 103, 189, 0.8)', 'rgba(140, 86, 75, 0.8)', 'rgba(227, 119, 194, 0.8)', 'rgba(127, 127, 127, 0.8)','rgba(44, 160, 44, 0.8)' ]

# Création du Sankey diagram
fig = go.Figure(data=[go.Sankey(
    node=dict(
      pad=15,
      thickness=20,
      line=dict(color="black", width=0.5),
      label=sources,
      color=colors
    ),
    link=dict(
      source=link_source,
      target=link_target,
      value=link_value
  ))])

# Mise en forme du layout
fig.update_layout(title_text="Energy Distribution Sankey Diagram")

# fig.write_html(f"figures/{country_name}_optim_sankey_max.html")
# Afficher le diagramme
fig.show()